In [103]:
import pandas as pd
import requests
import json
from pandas import json_normalize
import logging

logging.basicConfig(filename='data_retrieval.log', level=logging.INFO)


In [52]:
sid = '09dceb980747489297e7ea0a51077a66'
skey = 'f3543385c18c48cd98018f4cc39bf12a'
baseURL = 'https://api.spotify.com'


### Endpoints

In [91]:
def request_access_token(cid = sid, skey = skey ):
    url = "https://accounts.spotify.com/api/token"
    headers = {
        "Content-Type": "application/x-www-form-urlencoded"
    }
    data = {
        "grant_type": "client_credentials",
        "client_id": cid,
        "client_secret": skey
    }

    response = requests.post(url, headers=headers, data=data)
    if response.status_code == 200:
        return response.json().get('access_token')
    else:
        print(f"Failed to obtain token, status code: {response.status_code}")
        return None

def fetch_tracks_info(track_ids):
    ids = ','.join(track_ids)
    url = f"https://api.spotify.com/v1/tracks?ids={ids}"

    response = requests.get(url, headers=headers)
    
    return response


### Endpoint utils

In [133]:
def new_session_headers():
    headers = {
        "Authorization": f'Bearer {request_access_token()}',
    }

    return headers

In [134]:
headers = new_session_headers()

### Core data

In [178]:
all_files = [f"./data_2022/MyData_streaming_hist/endsong_{i}.json" for i in range(12)]
df_list = [pd.read_json(file) for file in all_files]
df = pd.concat(df_list, ignore_index=True)
df.ts = pd.to_datetime(df.ts)

non_tracks = df.loc[df.spotify_track_uri.str.contains('track') != True].index
df.drop(index=non_tracks, inplace=True)

df = df.sort_values(by='ts').reset_index(drop = True)

df = df[['spotify_track_uri', 'ts']].copy()

### Metadata retrieval

In [141]:
def get_batch_metadata(batch_list, start_id=0, end_id=1):
    fetched_info = fetch_tracks_info(batch_list)
    if fetched_info.status_code == 200:
        fetched_info = json.loads(fetched_info.text)
        frames = [json_normalize(track) for track in fetched_info['tracks']]
        df = pd.concat(frames, ignore_index=True)

        return df
    else:
        r = f"Failed for IDs {start_id} to {end_id}. Message: {fetched_info.status_code} {json.loads(fetched_info.text)['error']['message']}"
        logging.error(r)
        print(r)
        return r

def save_data(data, start_id, end_id):
    data.to_csv(f'fetched_data/track_data_{start_id}', index = False)
    logging.info(f'Data saved from {start_id} to {end_id}')

    return True

In [135]:
batch_list = ['7crplFzt7spG80NCbpmuCp', '1tYt8PbpbeTuqsNmprAZYY']

t = get_batch_metadata(batch_list)

In [179]:
start_id = df.index.start
end_id = df.index.stop

chunk_size = 100
for start in range(0, len(df), chunk_size):
    end = start + chunk_size
    chunk = df[start:end]
    batch_list = list(chunk.spotify_track_uri.apply(lambda x: x.split(':')[-1])) #get just spotify id from uri
    print(batch_list)


['7crplFzt7spG80NCbpmuCp', '1tYt8PbpbeTuqsNmprAZYY', '52izjvF7wwveRG1rDJsGWe', '1xQv4unOladJFtLUOy2eb7', '3vv9phIu6Y1vX3jcqaGz5Z', '0r4SsYcwvd8URat6AS2m6f', '6WhzFzROw3aq3rPWjgYlxr', '37k7igIs7IrMVUadwWKHJ6', '6Knv6wdA0luoMUuuoYi2i1', '6WjmPTZKeDylStKmGHLcqQ', '6mNMp0g3zkg1K7uBpn07zl', '6NljjfZDdfVh8x31Dwvj7J', '2MNv9hlHsQUlxG00IKNxUY', '3G2grVPTDrTQskKKsoEnRA', '0PaemlGLiH2O6nAxRCzmee', '7L5jgZtAyfiU7elB8DIqCx', '6splO3UF8hSmK33y5fJTNk', '3FQdtOMXdfDcDDjY1OHAqz', '2Pjazbe7W5svzVZt1sBtb1', '6WLS56xiRrXjSm9RSdL3zD', '2H8LPaY3NSjmOFMH2Rygnz', '0w3Q3VFdrYzo24QUIGnBNy', '1omIb7BrAk7qwRrCSHJTc5', '2OkU57LVQoynnVyLE1LrPN', '4oHmgneU9dwYoqg0SJSOCf', '3NBDgwEAGMj0aKRsU8zoO9', '203t5YqpCFmIdxj8hIotxo', '42JmSZ977by4p0AW0y558P', '5IDra44Yb9g0GHzZCn1vX4', '2QTp2o96FG61yVAxZTHqSV', '5snyhxAh55A2wlNRH7VVZJ', '0z8yrlXSjnI29Rv30RssNI', '73JYmIV6UitbrIDyGb2lWf', '4n5wWTTgnLtb8nVwPWVzgx', '76fM7d7hS1jHSzCGIy69DN', '7tSMnub7dlynTcPGwvjOMP', '7yiAjQfyR6f2AJ8sxlRect', '3PnOOmkxruDDAiMYZZTgO7', '2d29B8frPb

In [180]:
df.loc[df.spotify_track_uri.str.contains('track') != True].index

Index([], dtype='int64')

In [155]:
for i in range(0, len(df), chunk_size):
    print(i)

0
100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200
11300
11400
11500
11600
11700
11800
11900
12000
12100
12200
12300
12400
12500
12600
12700
12800
12900
13000
13100
13200
13300
13400
13500
13600
13700
13800
13900
14000
14100
14200
14300
14400
14500
14600
14700
14800
14900
15000
15100
15200
15300
15400
15500
15600
15700
15800
15900
16000
16100
16200
16300
16400
16500
16600
16700
16800
16900
17000
17100
17200
17300
17400
17500
17600
17700
17800
17900
18000
18100
18200
18300
18400
18